#Group : 14

Malika Lal 12220004

Snigdha Bhattacharjee 12220067

Deepak Sahu 12220074

Aadarsh Mohapatra 12220033


## Staging Zone


In [0]:
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.sql.types import StructType, StructField, StringType, IntegerType

spark.conf.set("spark.sql.legacy.timeParserPolicy","LEGACY")

In [0]:
from pyspark.sql import SparkSession

spark = SparkSession.builder \
  .appName("Databricks Shell") \
  .config("spark.sql.hive.metastorePartitionPruningFallbackOnException", "true") \
  .getOrCreate()

These lines import the required modules from PySpark. SparkSession is used to interact with Spark, and functions and types from pyspark.sql are imported for various data manipulation and structuring operation

In [0]:
%sql

USE landing_orders; ---- to switch to the landing_orders database.
SHOW Tables; ---- to display the list of tables in the current database.

database tableName isTemporary landing_orders customermaster false landing_orders orders false

## Loading Data into the Staging Zone

In order to load data into the staging zone with a structure suitable for querying in the curated zone, it is necessary to create a staging data zone. This involves utilizing SQL queries to load table data from the landing zone. During the data loading process, essential transformations have been applied, including the addition of a converted-month column to enhance query output readability.


In [0]:
%sql 
-- Drop (if exists) and create a staging database

DROP DATABASE IF EXISTS staging_sales CASCADE;

CREATE DATABASE staging_sales;

In [0]:
%fs rm -r dbfs:/user/hive/warehouse/staging_sales.db/orders

res1: Boolean = false

The %fs rm -r command is used in Databricks notebooks to recursively remove files and directories  dbfs:/user/hive/warehouse/staging_sales.db/orders.

In [0]:
sql_query_drop = """
DROP TABLE IF EXISTS staging_sales.orders
"""

sql_query_create = """
CREATE TABLE staging_sales.orders
USING DELTA
PARTITIONED BY (Category)
AS
SELECT
  CAST(Order_Id AS INT) AS Order_Id,
  date_format(Order_Date, 'yyyy-MM-dd') AS Order_Date,
  Status,
  CAST(Item_Id AS INT) AS Item_Id,
  CAST(Qty_Ordered AS INT) AS Qty_Ordered,
  CAST(Price AS DECIMAL(18,6)) AS Price,
  CAST(Value AS DECIMAL(18,6)) AS Value,
  CAST(Discount_Amount AS DECIMAL(18,6)) AS Discount_Amount,
  CAST(Total AS DECIMAL(18,6)) AS Total,
  Category,
  Payment_Method,
  CAST(Cust_Id AS INT) AS Cust_Id,
  CAST(Year AS INT) AS Year,
  Month,
  CONCAT(CAST(MONTH(FROM_UNIXTIME(UNIX_TIMESTAMP(month, 'MMM-yyyy'))) AS STRING), '/', CAST(year AS STRING)) AS Converted_Month
FROM
  landing_orders.orders
"""

sql_query_select = """
SELECT * FROM staging_sales.orders
"""

# Execute the queries
spark.sql(sql_query_drop)
spark.sql(sql_query_create)
result_df = spark.sql(sql_query_select)
result_df.show()


+---------+----------+--------------+-------+-----------+-----------+-----------+---------------+-----------+----------+---------------+-------+----+--------+---------------+
| Order_Id|Order_Date|        Status|Item_Id|Qty_Ordered|      Price|      Value|Discount_Amount|      Total|  Category| Payment_Method|Cust_Id|Year|   Month|Converted_Month|
+---------+----------+--------------+-------+-----------+-----------+-----------+---------------+-----------+----------+---------------+-------+----+--------+---------------+
|100443891|2021-02-08|      canceled| 727605|          2| 889.500000| 889.500000|       0.000000| 889.500000|Appliances|        Easypay|  67276|2021|Feb-2021|         2/2021|
|100443912|2021-02-08|order_refunded| 727652|          2| 408.900000| 408.900000|       0.000000| 408.900000|Appliances|        Easypay|  67276|2021|Feb-2021|         2/2021|
|100446070|2021-02-19|      canceled| 731868|          2| 799.900000| 799.900000|       0.000000| 799.900000|Appliances|     

Creating a Data Pipeline: Loading Orders Table into Staging Zone
A data pipeline has been established to efficiently load data from the "orders" table into the staging zone. This process involves applying column transformations to enhance query execution and optimize the structure of the data in the staging zone.


In [0]:
%sql
SELECT * FROM staging_sales.orders limit 10; --- Viewing data

Order_Id Order_Date Status Item_Id Qty_Ordered Price Value Discount_Amount Total Category Payment_Method Cust_Id Year Month Converted_Month 100443891 2021-02-08 canceled 727605 2 889.500000 889.500000 0.000000 889.500000 Appliances Easypay 67276 2021 Feb-2021 2/2021 100443912 2021-02-08 order_refunded 727652 2 408.900000 408.900000 0.000000 408.900000 Appliances Easypay 67276 2021 Feb-2021 2/2021 100446070 2021-02-19 canceled 731868 2 799.900000 799.900000 0.000000 799.900000 Appliances Easypay 67276 2021 Feb-2021 2/2021 100446072 2021-02-19 canceled 731870 2 420.000000 420.000000 0.000000 420.000000 Appliances Easypay 67276 2021 Feb-2021 2/2021 100381014 2020-12-19 canceled 617311 2 3000.000000 3000.000000 0.000000 3000.000000 Appliances Easypay 67279 2020 Dec-2020 12/2020 100381225 2020-12-19 complete 617861 2 3000.000000 3000.000000 0.000000 3000.000000 Appliances easypay_voucher 67279 2020 Dec-2020 12/2020 100423095 2020-12-28 received 691380 2 139.900000 139.900000 0.000000 139.900000 Appliances cod 67279 2020 Dec-2020 12/2020 100381054 2020-12-19 order_refunded 617420 2 164.900000 164.900000 0.000000 164.900000 Appliances cod 67294 2020 Dec-2020 12/2020 100381055 2020-12-19 canceled 617421 2 638.200000 638.200000 95.730000 542.470000 Appliances Easypay 67295 2020 Dec-2020 12/2020 100381076 2020-12-19 canceled 617455 2 638.200000 638.200000 95.730000 542.470000 Appliances Easypay 67295 2020 Dec-2020 12/2020

In [0]:

%fs rm -r dbfs:/user/hive/warehouse/staging_sales.db/customermaster


res3: Boolean = true

Removing file and directories from dbfs:/user/hive/warehouse/staging_sales.db/customermaster

In [0]:
%sql
--Define the customer schema for the DataFrame
DROP TABLE IF EXISTS staging_sales.customermaster;
CREATE TABLE staging_sales.customermaster
USING PARQUET
OPTIONS (
  'compression' 'SNAPPY'
)
AS
SELECT
  city,
  county,
   CustomerSince,
  EMail,
  Gender,
  PlaceName,
  Region,
  State,
  Zip,
  cast(age as int),
  cast(cust_id as int),
  split(full_name, ',')[0] AS firstname,
  split(full_name, ',')[1] AS Lastname
FROM
  landing_orders.customermaster;

In this process, customer data from the landing zone is efficiently loaded into the staging zone using SQL utility. 
During the loading phase, essential transformations are applied to optimize the structure of the data in the staging zone. 
Additionally, two new columns, namely "First Name" and "Last Name," have been created to enhance the dataset.

In [0]:
%sql
SELECT * from staging_sales.customermaster--- View the customer master data

city county CustomerSince EMail Gender PlaceName Region State Zip age cust_id firstname Lastname Duluth St. Louis 2007-08-15 katlyn.michels@gmail.com F Duluth Midwest MN 55805 21 72612 Michels Katlyn Forsyth Rosebud 2004-10-29 lezlie.kucera@yahoo.com F Forsyth West MT 59327 63 72613 Kucera Lezlie Miami Miami-Dade 2010-09-03 king.bodie@outlook.com M Miami South FL 33199 35 17771 Bodie King Saint John Whitman 2005-08-22 antione.ouzts@microsoft.com M Saint John West WA 99171 36 72614 Ouzts Antione White Lake Sullivan 2006-11-17 devon.lepley@gmail.com M White Lake Northeast NY 12786 55 72615 Lepley Devon Butte Silver Bow 2001-04-11 leonel.yarnell@microsoft.com M Butte West MT 59750 40 72616 Yarnell Leonel Oakdale Antelope 2016-06-28 cleotilde.cowman@walmart.com F Oakdale Midwest NE 68761 30 72617 Cowman Cleotilde Dimondale Eaton 2010-06-04 kelly.favela@cox.net M Dimondale Midwest MI 48821 58 72618 Favela Kelly Oklahoma City Oklahoma 1997-01-09 leeann.brumbelow@yahoo.com F Oklahoma City South OK 73193 24 72619 Brumbelow Leeann Colorado City Pueblo 2017-01-24 willard.rezendes@gmail.com M Colorado City West CO 81019 67 72620 Rezendes Willard San Carlos San Mateo 2016-03-29 haywood.brodie@gmail.com M San Carlos West CA 94070 56 72621 Brodie Haywood Indianapolis Marion 2015-12-19 carmelo.dinger@aol.com M Indianapolis Midwest IN 46278 64 72622 Dinger Carmelo Crestone Saguache 1992-12-06 youlanda.biondi@yahoo.com F Crestone West CO 81131 54 72623 Biondi Youlanda Fitzpatrick Bullock 1988-06-26 tiffany.redding@ibm.com F Fitzpatrick South AL 36029 23 72624 Redding Tiffany Dayton Montgomery 2010-07-13 dalia.blaisdell@gmail.com F Dayton Midwest OH 45481 62 72625 Blaisdell Dalia Mentcle Indiana 2017-05-08 alita.lent@gmail.com F Mentcle Northeast PA 15761 30 72626 Lent Alita Sikeston Scott 2001-05-25 charles.burroughs@yahoo.co.in M Sikeston Midwest MO 63801 37 72627 Burroughs Charles Milwaukee Milwaukee 2008-07-14 brice.hartness@aol.com M Milwaukee Midwest WI 53203 62 72628 Hartness Brice Halsey Thomas 1988-01-30 toccara.mccool@hotmail.com F Halsey Midwest NE 69142 39 72629 Mccool Toccara Easton Kittitas 2017-01-25 perry.manchester@hotmail.com F Easton West WA 98925 45 72630 Manchester Perry Celina Collin 1993-05-02 gil.berryhill@gmail.com M Celina South TX 75009 21 72631 Berryhill Gil Berkshire Berkshire 2017-01-13 augustina.rogalski@comcast.net F Berkshire Northeast MA 1224 61 72632 Rogalski Augustina Fort Mitchell Russell 1998-09-03 kim.dials@comcast.net F Fort Mitchell South AL 36856 35 72633 Dials Kim Nilwood Macoupin 2008-10-14 anibal.chase@ibm.com M Nilwood Midwest IL 62672 41 18540 Chase Anibal Haskell Muskogee 2016-10-29 jess.silvers@yahoo.com M Haskell South OK 74436 36 72634 Silvers Jess Yreka Siskiyou 2014-01-11 tori.cicero@aol.com F Yreka West CA 96097 30 72635 Cicero Tori Longlake McPherson 1993-04-10 lavern.jessie@shell.com M Longlake Midwest SD 57457 31 72636 Jessie Lavern Springfield Sangamon 1982-10-10 herb.hohn@gmail.com M Springfield Midwest IL 62719 73 57842 Hohn Herb Brilliant Marion 2006-01-08 hipolito.messersmith@yahoo.com M Brilliant South AL 35548 36 72637 Messersmith Hipolito Canton Stark 1993-06-05 gus.winkle@aol.com M Canton Midwest OH 44708 22 72638 Winkle Gus Hollywood Charleston 2014-01-25 lillian.bugg@yahoo.com F Hollywood South SC 29449 45 72639 Bugg Lillian Gypsum Ottawa 2000-12-06 tomi.parmelee@yahoo.com F Gypsum Midwest OH 43433 57 72640 Parmelee Tomi Pinedale Sublette 2009-12-15 ryan.meng@hotmail.com M Pinedale West WY 82941 55 72641 Meng Ryan Chester Chester 2006-06-20 shemika.hammel@shell.com F Chester South SC 29706 49 72642 Hammel Shemika Mystic New London 2014-07-12 darrick.astudillo@ntlworld.com M Mystic Northeast CT 6355 69 72643 Astudillo Darrick Las Vegas Clark 2005-07-06 cherise.gambrel@aol.com F Las Vegas West NV 89141 30 72644 Gambrel Cherise Proctorville Robeson 2010-08-04 carolann.tussey@sbcglobal.net F Proctorville South NC 28375 68 72645 Tussey Carolann Hanna McIntosh 2004-03-29 herschel.feh